In [96]:
import pandas as pd
import numpy as np
import nltk
import jieba #for tokenizing Chinese
import seaborn as sns
import matplotlib.pyplot as plt
import plotly.express as px
import collections
import re

In [97]:
#reference here: https://www.kaggle.com/noxmoon/chinese-official-daily-news-since-2016/downloads/chinese-official-daily-news-since-2016.zip/1


df = pd.read_csv('chinese_news.csv')
print(df.shape)
print(df.columns)
#详细全文” some relatively long news, "国内“ domestic short news, "国际“ international short news.
print(df.head())

(20738, 4)
Index(['date', 'tag', 'headline', 'content'], dtype='object')
         date   tag                                           headline  \
0  2016-01-01  详细全文  陆军领导机构火箭军战略支援部队成立大会在京举行 习近平向中国人民解放军陆军火箭军战略支援部队...   
1  2016-01-01  详细全文                             中央军委印发《关于深化国防和军队改革的意见》   
2  2016-01-01  详细全文                           《习近平关于严明党的纪律和规矩论述摘编》出版发行   
3  2016-01-01  详细全文                                 以实际行动向党中央看齐 向高标准努力   
4  2016-01-01  详细全文                                 【年终特稿】关键之年 改革挺进深水区   

                                             content  
0  中国人民解放军陆军领导机构、中国人民解放军火箭军、中国人民解放军战略支援部队成立大会2015...  
1  经中央军委主席习近平批准，中央军委近日印发了《关于深化国防和军队改革的意见》。\n《意见》强...  
2  由中共中央纪律检查委员会、中共中央文献研究室编辑的《习近平关于严明党的纪律和规矩论述摘编》一...  
3  广大党员干部正在积极学习习近平总书记在中央政治局专题民主生活会上的重要讲话。大家纷纷表示要把...  
4  刚刚过去的2015年，是全面深化改革的关键之年。改革集中发力在制约经济社会发展的深层次矛盾，...  


In [98]:
df['date'].describe()

count          20738
unique          1008
top       2018-09-05
freq              42
Name: date, dtype: object

In [99]:
df['tag'].value_counts()

详细全文    11534
国内       6186
国际       3018
Name: tag, dtype: int64

In [100]:
'''
So what do we need to do? What's our hypothesis?
I'd be interested to see if there is any favorable news of Xi Jinping
    a. Or if the number of news pieces increased around the time that he changed the constitution in feb/march 2018.
    

1. Find out how many articles mention 习近平?
     1a. plot those vs. time
2. See the most common words in total articles
    2a. See the most common words in articles with Xi Jinping and compare to overall most common?
    2b. Predict if an article is about Xi Jinping based on the words it has in it. It can be a Xi-filter!
    

'''
#we only need the date and content for this particular analysis
subset = pd.DataFrame(df[['date', 'content']].astype('str'))

def cutword(x):
        seg = jieba.cut(x, cut_all=False) 
        return ' '.join(seg)



subset['tokenized'] = subset['content'].apply(cutword)

subset.head()
    

date                                            content  \
0  2016-01-01  中国人民解放军陆军领导机构、中国人民解放军火箭军、中国人民解放军战略支援部队成立大会2015...   
1  2016-01-01  经中央军委主席习近平批准，中央军委近日印发了《关于深化国防和军队改革的意见》。\n《意见》强...   
2  2016-01-01  由中共中央纪律检查委员会、中共中央文献研究室编辑的《习近平关于严明党的纪律和规矩论述摘编》一...   
3  2016-01-01  广大党员干部正在积极学习习近平总书记在中央政治局专题民主生活会上的重要讲话。大家纷纷表示要把...   
4  2016-01-01  刚刚过去的2015年，是全面深化改革的关键之年。改革集中发力在制约经济社会发展的深层次矛盾，...   

                                           tokenized  
0  中国人民解放军 陆军 领导 机构 、 中国人民解放军 火箭 军 、 中国人民解放军 战略 支...  
1  经 中央军委 主席 习近平 批准 ， 中央军委 近日 印发 了 《 关于 深化 国防 和 军...  
2  由 中共中央纪律检查委员会 、 中共中央文献研究室 编辑 的 《 习近平 关于 严明 党的纪...  
3  广大党员 干部 正在 积极 学习 习近平 总书记 在 中央政治局 专题 民主 生活 会上 的...  
4  刚刚 过去 的 2015 年 ， 是 全面 深化改革 的 关键 之 年 。 改革 集中 发力...

In [101]:
def create_xi_count(row):
    return 100 * (row.count('习近平')/len(row))

subset['xi_count'] = subset['tokenized'].apply(create_xi_count)

subset.head()

date                                            content  \
0  2016-01-01  中国人民解放军陆军领导机构、中国人民解放军火箭军、中国人民解放军战略支援部队成立大会2015...   
1  2016-01-01  经中央军委主席习近平批准，中央军委近日印发了《关于深化国防和军队改革的意见》。\n《意见》强...   
2  2016-01-01  由中共中央纪律检查委员会、中共中央文献研究室编辑的《习近平关于严明党的纪律和规矩论述摘编》一...   
3  2016-01-01  广大党员干部正在积极学习习近平总书记在中央政治局专题民主生活会上的重要讲话。大家纷纷表示要把...   
4  2016-01-01  刚刚过去的2015年，是全面深化改革的关键之年。改革集中发力在制约经济社会发展的深层次矛盾，...   

                                           tokenized  xi_count  
0  中国人民解放军 陆军 领导 机构 、 中国人民解放军 火箭 军 、 中国人民解放军 战略 支...  0.495050  
1  经 中央军委 主席 习近平 批准 ， 中央军委 近日 印发 了 《 关于 深化 国防 和 军...  0.060386  
2  由 中共中央纪律检查委员会 、 中共中央文献研究室 编辑 的 《 习近平 关于 严明 党的纪...  0.398010  
3  广大党员 干部 正在 积极 学习 习近平 总书记 在 中央政治局 专题 民主 生活 会上 的...  0.338983  
4  刚刚 过去 的 2015 年 ， 是 全面 深化改革 的 关键 之 年 。 改革 集中 发力...  0.128590

In [102]:
#drop rows that don't have xi jinping
xi_subset = subset[subset['xi_count'] > 0.0]


In [103]:
fig = px.scatter(subset, x="date", y="xi_count", title='Mentions of Xi as percentage of article')
fig.show()

In [104]:
subset['tokenized'].shape

(20738,)

In [105]:

def create_filtered_dict(series):
    wordcount = {}
    for token in series:
        #this function creates a dictionary key for each row of the df
        #it strips all punctuation, and removes any identical articles (there are a couple)
        
        token = token.replace("。","")
        token = token.replace("，","")
        token = token.replace("、","")
        token = token.replace("：","")
        token = token.replace("？","")
        token = token.replace("！","")
        token = token.replace("\n", "")
        token = token.replace("“", "")
        token = token.replace("”", "")
        token = token.replace("《", "")
        token = token.replace("》", "")
        if token not in wordcount:
            wordcount[token] = 1
        else:
            wordcount[token] += 1
                
    return wordcount

#this cleaned dictionary can then be accessed with cleaned_dict.keys()
cleaned_all_dict = create_filtered_dict(subset['content'])
cleaned_xi_dict = create_filtered_dict(xi_subset['content'])

{'中国人民解放军陆军领导机构中国人民解放军火箭军中国人民解放军战略支援部队成立大会2015年12月31日在八一大楼隆重举行中共中央总书记国家主席中央军委主席习近平向陆军火箭军战略支援部队授予军旗并致训词代表党中央和中央军委向同志们向全军部队致以热烈祝贺强调要坚持以党在新形势下的强军目标为引领深入贯彻新形势下军事战略方针全面实施改革强军战略坚定不移走中国特色强军之路时刻听从党和人民召唤忠实履行党和人民赋予的神圣使命为实现中国梦强军梦作出新的更大的贡献下午4时成立大会开始全场高唱国歌仪仗礼兵护卫着鲜艳军旗正步行进到主席台前习近平将军旗郑重授予陆军司令员李作成政治委员刘雷火箭军司令员魏凤和政治委员王家胜战略支援部队司令员高津政治委员刘福连陆军火箭军战略支援部队主要领导军容严整精神抖擞向习近平敬礼从习近平手中接过军旗全场官兵向军旗敬礼授旗仪式后习近平致训词他指出成立陆军领导机构火箭军战略支援部队是党中央和中央军委着眼实现中国梦强军梦作出的重大决策是构建中国特色现代军事力量体系的战略举措必将成为我军现代化建设的一个重要里程碑载入人民军队史册习近平强调陆军是党最早建立和领导的武装力量历史悠久敢打善战战功卓著为党和人民建立了不朽功勋陆军对维护国家主权安全和发展利益具有不可替代的作用陆军全体官兵要弘扬陆军光荣传统和优良作风适应信息化时代陆军建设模式和运用方式的深刻变化探索陆军发展特点和规律按照机动作战立体攻防的战略要求加强顶层设计和领导管理优化力量结构和部队编成加快实现区域防卫型向全域作战型转变努力建设一支强大的现代化新型陆军习近平强调火箭军是我国战略威慑的核心力量是我国大国地位的战略支撑是维护国家安全的重要基石火箭军全体官兵要把握火箭军的职能定位和使命任务按照核常兼备全域慑战的战略要求增强可信可靠的核威慑和核反击能力加强中远程精确打击力量建设增强战略制衡能力努力建设一支强大的现代化火箭军习近平强调战略支援部队是维护国家安全的新型作战力量是我军新质作战能力的重要增长点战略支援部队全体官兵要坚持体系融合军民融合努力在关键领域实现跨越发展高标准高起点推进新型作战力量加速发展一体发展努力建设一支强大的现代化战略支援部队习近平强调你们要坚持以党在新形势下的强军目标为引领深入贯彻新形势下军事战略方针全面实施改革强军战略坚定不移走中国特色强军之路时刻听从党和人民的召唤忠诚履行党和人民赋予的神

In [121]:

def getcount(dict):
    #creates empty dict
    wordcount = {}
    for k in dict.keys():
        #gets tokenized words (usually a combination of 2+ characters)
        words = jieba.cut(k, cut_all=False) 
        #adds them all to the wordcount dict, and with a value = number of times they've appeared
        for word in words: 
            if word not in wordcount.keys(): 
                wordcount[word] = 1
            else: 
                wordcount[word] += 1                
    return wordcount
    
count = getcount(cleaned_all_dict)
xi_count = getcount(cleaned_xi_dict)
#print(sorted(count.items(), key=lambda kv: kv[1], reverse=True))

[('的', 139797), ('在', 43293), ('和', 41323), ('了', 32978), ('发展', 20403), ('是', 19083), ('中国', 18765), ('等', 15784), ('为', 15549), ('要', 13484), ('习近平', 13407), ('将', 13295), ('合作', 12319), ('对', 12014), ('新', 11656), ('年', 11627), ('国家', 10872), ('日', 10580), ('中', 10519), ('工作', 9310), ('与', 8938), ('建设', 8324), ('上', 8182), ('月', 8171), ('也', 7665), ('表示', 7346), ('经济', 7236), ('有', 7016), ('到', 6887), ('以', 6864), ('主席', 6776), ('推动', 6271), ('问题', 6253), ('大', 6178), ('全面', 6150), ('加强', 6140), ('并', 6129), ('推进', 6049), ('今天', 5998), ('改革', 5905), ('就', 5753), ('从', 5728), ('重要', 5599), ('个', 5509), ('会议', 5379), ('我国', 5266), ('全国', 5232), ('创新', 5190), ('进行', 5184), ('；', 5084), ('国际', 5031), ('他', 4998), ('实现', 4980), ('还', 4963), ('企业', 4863), ('地区', 4814), ('向', 4811), ('人', 4710), ('坚持', 4674), ('说', 4648), ('组织', 4585), ('把', 4566), ('人民', 4547), ('关系', 4541), ('领域', 4510), ('这', 4491), ('号', 4480), ('党', 4406), ('后', 4390), ('通过', 4386), ('美国', 4302), ('总书记', 4247), ('世界',

In [118]:
#DO MORE RESEARCH ABOUT HOW THIS WORKS OR IF THIS IS NECESSARY
#Potentially make the word count dictionaries dataframes so things like 的、在、和、了, etc. can be dropped
import heapq 
freq_words = heapq.nlargest(100, count, key=count.get)
freq_xi_words = heapq.nlargest(100, xi_count, key=xi_count.get)
print(freq_words)
print("\n")
print(freq_xi_words)

common_words = [x for x in freq_words if x in freq_xi_words]
print("\n")
print(common_words)

['的', '在', '和', '了', '发展', '是', '中国', '等', '为', '要', '习近平', '将', '合作', '对', '新', '年', '国家', '日', '中', '工作', '与', '建设', '上', '月', '也', '表示', '经济', '有', '到', '以', '主席', '推动', '问题', '大', '全面', '加强', '并', '推进', '今天', '改革', '就', '从', '重要', '个', '会议', '我国', '全国', '创新', '进行', '；', '国际', '他', '实现', '还', '企业', '地区', '向', '人', '坚持', '说', '组织', '把', '人民', '关系', '领域', '这', '号', '党', '后', '通过', '美国', '总书记', '世界', '都', '我们', '总统', '指出', '好', '今年', '让', '共同', '中方', '政治', '被', '各', '举行', '政府', '更', '战略', '不', '—', '代表', '强调', '目前', '支持', '精神', '李克强', '多', '社会', '下']


['的', '和', '在', '发展', '习近平', '了', '要', '中国', '合作', '是', '为', '新', '工作', '国家', '主席', '建设', '等', '中', '对', '推动', '加强', '全面', '总书记', '推进', '以', '重要', '经济', '坚持', '党', '大', '改革', '年', '人民', '上', '关系', '将', '日', '创新', '指出', '政治', '表示', '问题', '会议', '我们', '领域', '把', '强调', '中方', '社会主义', '实现', '好', '与', '战略', '同', '共同', '各', '精神', '时代', '国际', '党中央', '深化', '特色', '；', '思想', '并', '世界', '向', '也', '有', '双方', '更', '同志', '领导', '月', '中央', '就', '一路', '一带'

In [ ]:
#TAKES A LONG TIME TO RUN, BUT IS RETURNING AN ARRAY WITH WHETHER THE TOP 100 WORDS APPEAR IN EACH KEY OF THE DICT

X = [] 
for k in cleaned_all_dict.keys(): 
    vector = [] 
    for word in freq_words: 
        if word in jieba.cut(k, cut_all=False): 
            vector.append(1) 
        else: 
            vector.append(0) 
    X.append(vector) 
X = np.asarray(X) 

#print(X)

In [109]:
subset[subset['xi_count'] > 2.0]
#These are two outliers with high xi_counts because they have fewer characters than average
print(subset['content'].loc[6069])
print(subset['content'].loc[6085])

国家主席习近平在结束出席亚太经合组织第二十四次领导人非正式会议系列活动之后，当地时间21日开始对秘鲁进行国事访问。
当地时间上午9时45分，习近平和夫人彭丽媛抵达总统府。现场鸣21响礼炮，习近平和夫人彭丽媛乘车绕广场一周，习近平在总统府检阅仪仗队。习近平同库琴斯基亲切握手，军乐队奏中秘两国国歌。

军乐队奏中智两国国歌。在巴切莱特陪同下，习近平检阅陆军仪仗队。习近平向巴切莱特介绍中方陪同人员。巴切莱特向习近平介绍智方主要官员。习近平在巴切莱特陪同下检阅总统卫队。



In [110]:
#VERY NON-ELEGANT WAY TO GET THE AVERAGE LENGTH OF ARTICLES

def avg_len(row):
    length = 0
    length += len(row)
    return length

average = subset['tokenized'].apply(avg_len)

length = 0

for row in average:
    length += row

print(length/(len(subset)))

518.0969235220368
